### Intsall libraries

In [1]:
pip install h3

     |████████████████████████████████| 943 kB 4.4 MB/s eta 0:00:01
Note: you may need to restart the kernel to use updated packages.


In [2]:
pip install folium

     |████████████████████████████████| 102 kB 4.0 MB/s ta 0:00:01
Note: you may need to restart the kernel to use updated packages.


In [2]:
pip install geojson

Note: you may need to restart the kernel to use updated packages.


In [34]:
import h3
import json
import folium
from geojson.feature import *
import branca.colormap as cm 
from folium import Map, Marker, GeoJson 

import pandas as pd 

import warnings
warnings.filterwarnings('ignore')

## Loading data

In [35]:
A2B = pd.read_csv("A2B_Fare_Lookup.csv")
A2B.head()

partitionKey                    user_pseudo_id  \
0  62988560-2b0f-11ed-aeba-d39c8d7719af  1546E396FBFD49E6ACCB9BCBA42DBFE7   
1  51064c10-2cea-11ed-9a00-d5b713a64e81  1546E396FBFD49E6ACCB9BCBA42DBFE7   
2  76a63b10-2dcb-11ed-9a00-d5b713a64e81  1546E396FBFD49E6ACCB9BCBA42DBFE7   
3  5b83c8b9-e7eb-479e-a7fa-4e9c2a110036  1546E396FBFD49E6ACCB9BCBA42DBFE7   
4  bb0e3a30-2e95-11ed-9a00-d5b713a64e81  1546E396FBFD49E6ACCB9BCBA42DBFE7   

                 createdAt                                       startAddress  \
0  2022-09-03 08:34:19.703         2 Seaview Ave, Newport NSW 2106, Australia   
1  2022-09-05 17:14:01.170      181 Lawson St, Darlington NSW 2008, Australia   
2  2022-09-06 20:05:41.060     17 Millman Rd, Spring Farm NSW 2570, Australia   
3  2022-10-23 16:41:09.086        6/73 Albert St, Revesby NSW 2212, Australia   
4  2022-09-07 20:13:34.166  15 Warrigal St, Gregory Hills NSW 2557, Australia   

                                          endAddress  tripEstimate  BookingID  \
0  Sydney Airport DOM T2 Drop-Off, Sydney Airport...        126.00        NaN   
1  Sydney Airport DOM T2 Drop-Off, Sydney Airport...         30.66        NaN   
2  Sydney Airport DOM T2 Drop-Off, Sydney Airport...        158.76        NaN   
3  Sydney Airport DOM T2 Drop-Off, Sydney Airport...         68.99        NaN   
4  Sydney Airport DOM T2 Drop-Off, Sydney Airport...        160.65        NaN   

  BookingCreatedTime  PickUp_Latitude  PickUp_Longitude  DropOff_Latitude  \
0                NaN              NaN               NaN               NaN   
1                NaN              NaN               NaN               NaN   
2                NaN              NaN               NaN               NaN   
3                NaN              NaN               NaN               NaN   
4                NaN              NaN               NaN               NaN   

   DropOff_Longitude DispatchStatus  
0                NaN            NaN  
1                NaN            NaN  
2                NaN            NaN  
3                NaN            NaN  
4                NaN            NaN

### 先drop NaN 画地图

In [36]:
A2B.dropna(inplace=True)

In [37]:
A2B.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 521217 entries, 632261 to 1153632
Data columns (total 13 columns):
 #   Column              Non-Null Count   Dtype  
---  ------              --------------   -----  
 0   partitionKey        521217 non-null  object 
 1   user_pseudo_id      521217 non-null  object 
 2   createdAt           521217 non-null  object 
 3   startAddress        521217 non-null  object 
 4   endAddress          521217 non-null  object 
 5   tripEstimate        521217 non-null  float64
 6   BookingID           521217 non-null  float64
 7   BookingCreatedTime  521217 non-null  object 
 8   PickUp_Latitude     521217 non-null  float64
 9   PickUp_Longitude    521217 non-null  float64
 10  DropOff_Latitude    521217 non-null  float64
 11  DropOff_Longitude   521217 non-null  float64
 12  DispatchStatus      521217 non-null  object 
dtypes: float64(6), object(7)
memory usage: 55.7+ MB


In [38]:
### Transfer time format to pd datetime

A2B['BookingCreatedTime'] = pd.to_datetime(A2B['BookingCreatedTime'])

In [39]:
print("Date from : {}".format(A2B['BookingCreatedTime'].min()))
print("Date to   : {}".format(A2B['BookingCreatedTime'].max())) 

Date from : 2022-09-01 00:00:28.773000
Date to   : 2022-10-31 23:59:59.623000


### For this notebook we will use resulution 8 that has around 0.74 km^2 area for each hexagons.

In [43]:
resolution = 8 

df_map = A2B[["PickUp_Latitude", "PickUp_Longitude","DispatchStatus"]] #Dispatch是为了计算完成率

#-----------transfer geo to h3 coodinate----------#
df_map['hex_id'] = df_map.apply(lambda row: h3.geo_to_h3(
    row["PickUp_Latitude"], row["PickUp_Longitude"], resolution), axis = 1) 
    

In [44]:
#-----------count dispatch status----------#

df_aggreg = df_map.groupby('hex_id').agg({'DispatchStatus': ['count', lambda x: sum(x == 'Completed'), 
                                                     lambda x: sum(x == 'NotCompleted')]})

df_aggreg.columns = ['_'.join(col).rstrip('_') for col in df_aggreg.columns.values]
df_aggreg.reset_index(inplace=True) #把hex id从index移出来
df_aggreg.columns = ['hex_id','dispatch_quantity','completed_quantity','notcompleted_quantity']

df_aggreg['completion_rate'] = df_aggreg['completed_quantity']/df_aggreg['dispatch_quantity']


#Geometry_in h3
df_aggreg["geometry"] =  df_aggreg.hex_id.apply(lambda x: {"type" : "Polygon",
                    "coordinates": [h3.h3_to_geo_boundary(h=x,geo_json=True)]})

df_aggreg.sort_values(by = "completion_rate", ascending = False, inplace = True)

### 坐标转换成map能读懂的geojson格式

In [45]:
def heaxgons_df_to_geojson(df_hex,column_name = "completion_rate"):
    
    features_list = []
    
    for index,row in df_hex.iterrows():
        try:
            geometry_for_row = { "type" : "Polygon", "coordinates":
                                [h3.h3_to_geo_boundary(h=row["hex_id"],geo_json=True)]}
            
            feature = Feature(geometry = geometry_for_row , 
                              id=row["hex_id"], properties = {column_name : row[column_name]})
            
            features_list.append(feature)
        
        except:
            print("An exception occurred for hex " + row["hex_id"])
            
    features_collect = FeatureCollection(features_list)
    
    geojson_result = json.dumps(features_collect)
    
    return geojson_result

### 画图函数

In [117]:
def choropleth_map(df_aggreg, border_color = 'black', fill_opacity = 0.7, initial_map = None, with_legend = False,
                   kind = "filled_nulls"):  
    #colormap
    min_value = df_aggreg["completion_rate"].min()
    max_value = df_aggreg["completion_rate"].max()
    m = round ((min_value + max_value ) / 2 , 0)
    
    #take resolution from the first row
    res = h3.h3_get_resolution(df_aggreg.loc[0, 'hex_id'])

    
    if initial_map is None:
        initial_map = Map(location= [-33.78, 151.2], zoom_start=10, tiles="cartodbpositron", 
                attr= '© <a href="http://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors © <a href="http://cartodb.com/attributions#basemaps">CartoDB</a>' 
            )
        
    if kind == "linear":
        custom_cm = cm.LinearColormap(['green','yellow','red'], vmin=min_value, vmax=max_value)
    elif kind == "outlier":
        custom_cm = cm.LinearColormap(['blue','white','red'], vmin=min_value, vmax=max_value)
    elif kind == "filled_nulls":
        custom_cm = cm.LinearColormap(['#1E90FF','#3CB371','#DC143C'], 
                                      index=[0,m,max_value],vmin=min_value,vmax=max_value)

    #create geojson data from dataframe
    geojson_data = heaxgons_df_to_geojson(df_hex = df_aggreg)
    
    #plot on map
    name_layer = "Choropleth " + str(res)
    if kind != "linear":
        name_layer = name_layer + kind
        
    GeoJson(
        geojson_data,
        style_function = lambda feature: {
            'fillColor': custom_cm(feature['properties']['completion_rate']),
            'color': border_color,
            'weight': 1,
            'Highlight': True,
            'fillOpacity': fill_opacity 
        }, 
        name = name_layer
    ).add_to(initial_map)
    
    if with_legend == True:
        custom_cm.add_to(initial_map)   
    
    
    return initial_map

In [118]:
hexmap = choropleth_map(df_aggreg = df_aggreg, with_legend = True, kind = "filled_nulls") 

In [119]:
hexmap